# Star or Galaxy?

- [Schema Browser](https://skyserver.sdss.org/dr9/en/help/browser/browser.asp)
- SQL Query: 
```
SELECT pt.name, po.type, po.ra, po.dec, po.u, po.g, po.r, po.i, po.z
FROM PhotoObj po
JOIN PhotoType pt ON pt.value = po.type
```

 - [Flux magnitudes](https://voyages.sdss.org/preflight/light/filters/): u, g, r, i and z
    - total light/flux received
    - u’ – ultraviolet light
    - g’ – blue and green visible light
    - r’ – yellow and red visible light
    - i’ – near-infrared light
    - z’ – near-infrared light
columns: u-g, g-r, r-i, i-z
- We calculate redshift by measuring flux

In [1]:
import numpy as np
import pandas as pd

from sklearn.model_selection import train_test_split
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, hamming_loss, jaccard_score
from sklearn import tree
from sklearn.ensemble import RandomForestRegressor, RandomForestClassifier
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score, explained_variance_score, confusion_matrix

import pydotplus
from IPython.display import Image

In [2]:
## find median of train/test result data
## !might need to convert to np arrays first
def median_diff(predicted, actual):
  median = np.median(np.abs(predicted-actual))
  return median

# compare the accuracy of the pediction againt the actual values
## print(calculate_rmsd(predictions, test_targets))
# validate the model and print the med_diff
# diff = validate_model(dtr, features, targets)

# control depth of Decision Tree
# dtr = DecisionTreeRegressor(max_depth=5)

In [3]:
raw_data = pd.read_csv('star_classification.csv')

In [4]:
data = raw_data[['u', 'g', 'r', 'i', 'z', 'class']]
data.dropna(how='any')

u          g          r          i          z   class
0      20.771816  18.526823  17.392050  16.887115  16.500648  GALAXY
1      20.190552  20.111183  20.003725  19.536736  19.366606     QSO
2      20.658936  19.767363  20.112465  19.771290  19.810503  GALAXY
3      22.210409  19.843256  18.377989  17.126400  16.440516    STAR
4      20.798119  19.537325  19.040367  18.827971  18.753901    STAR
...          ...        ...        ...        ...        ...     ...
34995  23.085131  21.569397  20.834072  20.722933  20.907196  GALAXY
34996  20.357796  17.785997  16.430876  15.680991  15.243793    STAR
34997  19.772184  18.459652  17.930784  17.697937  17.600065    STAR
34998  22.370825  21.071478  21.035301  20.940239  20.902151    STAR
34999  22.030209  21.828310  20.771177  19.878147  19.756248  GALAXY

[35000 rows x 6 columns]

In [5]:
data['class'].unique()

array(['GALAXY', 'QSO', 'STAR'], dtype=object)

In [6]:
dummies = pd.get_dummies(data["class"])
data = pd.concat([data, dummies], axis = 1)

In [7]:
data

u          g          r          i          z   class  GALAXY  \
0      20.771816  18.526823  17.392050  16.887115  16.500648  GALAXY    True   
1      20.190552  20.111183  20.003725  19.536736  19.366606     QSO   False   
2      20.658936  19.767363  20.112465  19.771290  19.810503  GALAXY    True   
3      22.210409  19.843256  18.377989  17.126400  16.440516    STAR   False   
4      20.798119  19.537325  19.040367  18.827971  18.753901    STAR   False   
...          ...        ...        ...        ...        ...     ...     ...   
34995  23.085131  21.569397  20.834072  20.722933  20.907196  GALAXY    True   
34996  20.357796  17.785997  16.430876  15.680991  15.243793    STAR   False   
34997  19.772184  18.459652  17.930784  17.697937  17.600065    STAR   False   
34998  22.370825  21.071478  21.035301  20.940239  20.902151    STAR   False   
34999  22.030209  21.828310  20.771177  19.878147  19.756248  GALAXY    True   

         QSO   STAR  
0      False  False  
1       True  False  
2      False  False  
3      False   True  
4      False   True  
...      ...    ...  
34995  False  False  
34996  False   True  
34997  False   True  
34998  False   True  
34999  False  False  

[35000 rows x 9 columns]

In [8]:
features = data.copy().drop(columns=['class', 'GALAXY', 'QSO', 'STAR'])
target = data.copy()[['GALAXY', 'QSO', 'STAR']]

In [9]:
X_train, X_test, y_train, y_test = train_test_split(features, target, random_state=42, test_size = 0.3)

In [10]:
model = DecisionTreeClassifier(random_state=42)

In [11]:
model.fit(X_train, y_train)

DecisionTreeClassifier(random_state=42)

In [12]:
y_pred = model.predict(X_test)
y_pred = pd.DataFrame(y_pred, columns=y_test.columns)

In [13]:
# Flatten the lists for sklearn metrics
y_test_flat = [item for sublist in y_test.to_numpy() for item in sublist]
y_pred_flat = [item for sublist in y_pred for item in sublist]

In [14]:
len(y_pred_flat)

13

In [15]:
# Calculate metrics
accuracy = accuracy_score(y_test, y_pred)
precision = precision_score(y_test, y_pred, average='samples')
recall = recall_score(y_test, y_pred, average='samples')
f1 = f1_score(y_test, y_pred, average='samples')

print("Accuracy:", accuracy)
print("Precision:", precision)
print("Recall:", recall)
print("F1-score:", f1)
# print("Hamming Loss:", hamming_loss_value)
# print("Jaccard Similarity:", jaccard_similarity)


Accuracy: 0.8458095238095238
Precision: 0.8458095238095238
Recall: 0.8458095238095238
F1-score: 0.8458095238095238


In [16]:
# Create DOT data
dot_data = tree.export_graphviz(
    model, out_file=None, feature_names=features.columns, class_names=["0", "1"], filled=True
)

# Draw graph
graph = pydotplus.graph_from_dot_data(dot_data)

# Show graph
Image(graph.create_png())

dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.25423 to fit



## Random forest

In [17]:
model_rf = RandomForestClassifier(random_state=42)
model_rf.fit(X_train, y_train)
y_pred = model_rf.predict(X_test)
y_pred = pd.DataFrame(y_pred, columns=y_test.columns)
# Flatten the lists for sklearn metrics
y_test_flat = [item for sublist in y_test.to_numpy() for item in sublist]
y_pred_flat = [item for sublist in y_pred for item in sublist]

accuracy = accuracy_score(y_test, y_pred)
precision = precision_score(y_test, y_pred, average='samples')
recall = recall_score(y_test, y_pred, average='samples')
f1 = f1_score(y_test, y_pred, average='samples')

print("Accuracy:", accuracy)
print("Precision:", precision)
print("Recall:", recall)
print("F1-score:", f1)

Accuracy: 0.8823809523809524
Precision: 0.8823809523809524
Recall: 0.8823809523809524
F1-score: 0.8823809523809524


/Users/alisonandrade/anaconda3/lib/python3.11/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in samples with no predicted labels. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
